### Importing Libraries

In [102]:
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
import matplotlib.pyplot as plt 

In [103]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
%matplotlib inline 

###  Datasets to be studied
 I) Confirmed Cases Dataset of COVID-19
 
 II) Death Cases Dataset of COVID-19
 
 III) Recovered Cases Dataset of COVID-19
 
 IV)Testing Dataset of COVID-19
 
 V) INFORM Risk Index dataset

####  Confirmed Cases of COVID-19 

In [104]:
# import os
# os.chdir('/kaggle/working')
# os.getcwd()
# print(os.listdir("../input"))

In [105]:
# Importing  Confirmed Cases Dataset
url_confirmed = 'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv'
df_confirmed = pd.read_csv(url_confirmed, index_col="Country/Region")
# df_confirmed = pd.read_csv("../input/covid19time-series-data/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv",
#                           header = 0, index_col="Country/Region")
df_confirmed.drop(['Lat', 'Long' ], axis=1, inplace=True)
df_confirmed.head(3)


Province/State  1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  \
Country/Region                                                               
Afghanistan               NaN        0        0        0        0        0   
Albania                   NaN        0        0        0        0        0   
Algeria                   NaN        0        0        0        0        0   

                1/27/20  1/28/20  1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  \
Country/Region                                                                
Afghanistan           0        0        0        0        0       0       0   
Albania               0        0        0        0        0       0       0   
Algeria               0        0        0        0        0       0       0   

                2/3/20  2/4/20  2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  \
Country/Region                                                           
Afghanistan          0       0       0       0       0       0       0   
Albania              0       0       0       0       0       0       0   
Algeria              0       0       0       0       0       0       0   

                2/10/20  2/11/20  2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                2/17/20  2/18/20  2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                2/24/20  2/25/20  2/26/20  2/27/20  2/28/20  2/29/20  3/1/20  \
Country/Region                                                                 
Afghanistan           1        1        1        1        1        1       1   
Albania               0        0        0        0        0        0       0   
Algeria               0        1        1        1        1        1       1   

                3/2/20  3/3/20  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  \
Country/Region                                                           
Afghanistan          1       1       1       1       1       1       4   
Albania              0       0       0       0       0       0       0   
Algeria              3       5      12      12      17      17      19   

                3/9/20  3/10/20  3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  \
Country/Region                                                                 
Afghanistan          4        5        7        7        7       11       16   
Albania              2       10       12       23       33       38       42   
Algeria             20       20       20       24       26       37       48   

                3/16/20  3/17/20  3/18/20  3/19/20  3/20/20  3/21/20  3/22/20  \
Country/Region                                                                  
Afghanistan          21       22       22       22       24       24       40   
Albania              51       55       59       64       70       76       89   
Algeria              54       60       74       87       90      139      201   

                3/23/20  3/24/20  3/25/20  3/26/20  3/27/20  3/28/20  3/29/20  \
Country/Region                                                                  
Afghanistan          40       74       84       94      110      110      120   
Albania             104      123      146      174      186      197      212   
Algeria             230      264      302      367      409      454      511   

                3/30/20  3/31/20  4/1/20  4/2/20  4/3/20  4/

#### Data Preprocessing for the dataset I

In [106]:
# Country grouping on original dataframe        
gr_confirmed = df_confirmed.groupby("Country/Region").sum()
# gr_confirmed.head(3)

In [107]:
# Checking for the missing values in the Confirmed Cases dataset

gr_confirmed.isnull().sum().sum()
gr_confirmed.isna().sum().sum()

# Hence, there are no missing values in our Confirmed Cases data. 

0

##### Shifting all data to one starting point & converting the Dates format to Days

Converting the Dates format to Days to bring all countries data to start from 1 starting point "Day1: 1"
Day1: 1,  is the day on which the confirmed cases for the country got greater than or equal to 10 

In [108]:
# Adding data for China (1-Jan to 21-Jan from a China CDC publication)
lab=[]
for i in range(1,22):
    lab.append("1/" + str(i) + "/20")
    gr_confirmed.insert(loc=i-1,column=lab[i-1], value=0)
gr_confirmed.loc["China"][0:10] = 20
gr_confirmed.loc["China"][10:21] = 310

# Remove Diamond princess and MS Zaandam
gr_confirmed = gr_confirmed.drop(["Diamond Princess", "MS Zaandam"])

# gr_confirmed.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Confirmed.csv")

gr_confirmed1= gr_confirmed.copy() # To have a copy of Confirmed Cases dataset in date format because ahead we are going to transform the data to days format
gr_confirmed1 = gr_confirmed1.reset_index()
# gr_confirmed1.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/Confirmed_datewise.csv")
# gr_confirmed.head(3)

# Dates are converted into no of days since 1/1/20 so that 1/1/20 corresponds to day 1
gr_confirmed_melt = gr_confirmed
dates = gr_confirmed_melt.keys()
FMT = '%m/%d/%y'

days = dates.map(lambda x: (datetime.strptime(x, FMT) - datetime.strptime("1/1/20", FMT)).days)

days = days + 1
# +1 is to start the days from 1 instead of 0

gr_confirmed_melt.columns = days # = dates will convert the columns to date formats again

x_lag = gr_confirmed_melt.ge(10).idxmax(axis=1) # x_lag gives position of first value in each row which is greater than or equal to 5

for i in range(gr_confirmed_melt.shape[0]): # gr_confirmed_melt.shape[0] = 187 (no. of rows) and gr_confirmed_melt.shape[1] = 138 (no. of columns)
    gr_confirmed_melt.iloc[i] = gr_confirmed_melt.iloc[i].shift(periods=-x_lag[i]+1) # all data shift to one starting point 
# gr_confirmed_melt.head(3)

# Melting our Confirmed Cases dataset

gr_confirmed_melt = gr_confirmed_melt.reset_index()
gr_confirmed_melt = pd.melt(gr_confirmed_melt,id_vars= "Country/Region", 
                       value_vars=days, var_name="Days", 
                       value_name="Confirmed Cases").sort_values(["Country/Region","Days"])

gr_confirmed_melt.set_index("Country/Region", inplace = True)
# gr_confirmed_melt.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/Confirmed_daywise_melted.csv")
# gr_confirmed_melt.shape
gr_confirmed_melt.head(5)

Days  Confirmed Cases
Country/Region                      
Afghanistan       1             11.0
Afghanistan       2             16.0
Afghanistan       3             21.0
Afghanistan       4             22.0
Afghanistan       5             22.0

#### Deaths due to COVID-19 

In [109]:
# Importing Deaths Dataset
url_death = 'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv'
df_death = pd.read_csv(url_death, index_col="Country/Region")
# df_death = pd.read_csv('../input/covid19time-series-data/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv', 
#                        header = 0, index_col="Country/Region")
df_death.drop(['Lat', 'Long'], axis=1, inplace=True)
df_death.head(3)

#df_death.to_csv("C:/Users/user/Downloads/COVID-19 Related info/time_series_COVID19-death.csv")

##### Data Preprocessing for the dataset II

# Country grouping on original dataframe        
gr_death = df_death.groupby("Country/Region").sum()
gr_death.head(3)

# # Now adding Australian dataframe
# gr_death = pd.concat([gr_death, Aust_death])

# Adding data for China (1-Jan to 20-Jan) 
lab=[]
for i in range(1,22):
    lab.append("1/" + str(i) + "/20")
    gr_death.insert(i-1,lab[i-1],0)
gr_death.loc["China"][0:10] = 1
gr_death.loc["China"][10:21] = 1

# Remove Diamond princess
gr_death = gr_death.drop(["Diamond Princess", "MS Zaandam"])
# gr_death.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Deaths.csv")

gr_death1 = gr_death.copy() # To have a copy of death dataset in date format because ahead we are going to transform the data to days format
gr_death1 = gr_death1.reset_index()
# gr_death1.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/Deaths_datewise.csv")

gr_death.head(3)

1/1/20  1/2/20  1/3/20  1/4/20  1/5/20  1/6/20  1/7/20  \
Country/Region                                                           
Afghanistan          0       0       0       0       0       0       0   
Albania              0       0       0       0       0       0       0   
Algeria              0       0       0       0       0       0       0   

                1/8/20  1/9/20  1/10/20  1/11/20  1/12/20  1/13/20  1/14/20  \
Country/Region                                                                
Afghanistan          0       0        0        0        0        0        0   
Albania              0       0        0        0        0        0        0   
Algeria              0       0        0        0        0        0        0   

                1/15/20  1/16/20  1/17/20  1/18/20  1/19/20  1/20/20  1/21/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  \
Country/Region                                                              
Afghanistan           0        0        0       0       0       0       0   
Albania               0        0        0       0       0       0       0   
Algeria               0        0        0       0       0       0       0   

                2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  \
Country/Region                                                             
Afghanistan          0       0       0       0       0        0        0   
Albania              0       0       0       0       0        0        0   
Algeria              0       0       0       0       0        0        0   

                2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                2/26/20  2/27/20  2/28/20  2/29/20  3/1/20  3/2/20  3/3/20  \
Country/Region                                                               
Afghanistan           0        0        0        0       0       0       0   
Albania               0        0        0        0       0       0       0   
Algeria               0        0        0        0       0       0       0   

                3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  3/9/20  3/10/20  \
Country/Region                                                            
Afghanistan          0       0       0       0       0       0        0   
Albania              0       0       0       0       0       0        0   
Algeria              0       0       0       0       0       0        0   

                3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  3/17/20  \
Country/Re

In [110]:
# Checking for the missing values in the death Cases dataset

gr_death.isnull().sum().sum()
gr_death.isna().sum().sum()

# Hence, there are no missing values in our death Cases data. 

0

##### Shifting all data to one starting point & converting the Dates format to Days
Converting the Dates format to Days to bring all countries data to start from 1 starting point "Day1: 1"
Day1: 1,  is the day on which the confirmed cases for the country got greater than or equal to 5 

In [111]:
# Dates are converted into no of days since 1/1/20 so that 1/1/20 corresponds to day 1
gr_death_melt = gr_death
dates = gr_death_melt.keys()
FMT = '%m/%d/%y'

days = dates.map(lambda x: (datetime.strptime(x, FMT) - datetime.strptime("1/1/20", FMT)).days)
days = days + 1
# +1 is to start the days from 1 instead of 0

gr_death_melt.columns = days # = dates will convert the columns to date formats again

x_lag  # x_lag gives position of first value in each row which is greater than or equal to 5 in confirmed cases dataset

for i in range(gr_death_melt.shape[0]): # gr_death_melt.shape[0] = 187 (no. of rows) and gr_death_melt.shape[1] = 138 (no. of columns)
    gr_death_melt.iloc[i] = gr_death_melt.iloc[i].shift(periods=-x_lag[i]+1) # all data shift to one starting point 
# gr_death_melt.head(3)

# Melting our Confirmed Cases dataset

gr_death_melt = gr_death_melt.reset_index()
gr_death_melt = pd.melt(gr_death_melt,id_vars= "Country/Region", 
                       value_vars=days, var_name="Days", 
                       value_name="Deaths").sort_values(["Country/Region","Days"])

gr_death_melt.set_index("Country/Region", inplace = True)
# gr_death_melt.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/Deaths_daywise_melted.csv")
# gr_death_melt.shape
gr_death_melt.head(5)

Days  Deaths
Country/Region             
Afghanistan       1     0.0
Afghanistan       2     0.0
Afghanistan       3     0.0
Afghanistan       4     0.0
Afghanistan       5     0.0

#### Recovered Cases of COVID-19

In [112]:
# Importing dataset for Recovered Cases
url_recovered = "https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv"
df_recovered = pd.read_csv(url_recovered, index_col="Country/Region")
# df_recovered = pd.read_csv("../input/covid19time-series-data/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv",
#                            header = 0, index_col="Country/Region")

df_recovered.drop(['Lat', 'Long'], axis=1, inplace=True)
df_recovered.head(3)

##### Data Prepocessing for dataset IV

# Country grouping on original dataframe        
gr_recovered = df_recovered.groupby("Country/Region").sum()

# Now adding Australian dataframe
# gr_death = pd.concat([gr_death, Aust_death])

# Adding data for China (1-Jan to 20-Jan) 
lab=[]
for i in range(1,22):
    lab.append("1/" + str(i) + "/20")
    gr_recovered.insert(i-1,lab[i-1],0)
gr_recovered.loc["China"][0:10] = 0
gr_recovered.loc["China"][10:21] = 0

# Remove Diamond princess
gr_recovered = gr_recovered.drop(["Diamond Princess", "MS Zaandam"])

# Adding the prefix to  all columns of Deaths dataset columns, which are dates to distingish them 
# from dates under Confirmed Cases dataset columns which are also same dates.
# gr_recovered = gr_recovered.add_prefix("Recovered Cases on ")
# gr_recovered.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Recovered.csv")
gr_recovered1 = gr_recovered.copy()  # To have a copy of Recovered Cases dataset in date format because ahead we are going to transform the data to days format
gr_recovered1 = gr_recovered1.reset_index()
# gr_recovered1.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/Recovered_datewise.csv")

# gr_recovered.shape
gr_recovered.head(3)

1/1/20  1/2/20  1/3/20  1/4/20  1/5/20  1/6/20  1/7/20  \
Country/Region                                                           
Afghanistan          0       0       0       0       0       0       0   
Albania              0       0       0       0       0       0       0   
Algeria              0       0       0       0       0       0       0   

                1/8/20  1/9/20  1/10/20  1/11/20  1/12/20  1/13/20  1/14/20  \
Country/Region                                                                
Afghanistan          0       0        0        0        0        0        0   
Albania              0       0        0        0        0        0        0   
Algeria              0       0        0        0        0        0        0   

                1/15/20  1/16/20  1/17/20  1/18/20  1/19/20  1/20/20  1/21/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                1/22/20  1/23/20  1/24/20  1/25/20  1/26/20  1/27/20  1/28/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                1/29/20  1/30/20  1/31/20  2/1/20  2/2/20  2/3/20  2/4/20  \
Country/Region                                                              
Afghanistan           0        0        0       0       0       0       0   
Albania               0        0        0       0       0       0       0   
Algeria               0        0        0       0       0       0       0   

                2/5/20  2/6/20  2/7/20  2/8/20  2/9/20  2/10/20  2/11/20  \
Country/Region                                                             
Afghanistan          0       0       0       0       0        0        0   
Albania              0       0       0       0       0        0        0   
Algeria              0       0       0       0       0        0        0   

                2/12/20  2/13/20  2/14/20  2/15/20  2/16/20  2/17/20  2/18/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                2/19/20  2/20/20  2/21/20  2/22/20  2/23/20  2/24/20  2/25/20  \
Country/Region                                                                  
Afghanistan           0        0        0        0        0        0        0   
Albania               0        0        0        0        0        0        0   
Algeria               0        0        0        0        0        0        0   

                2/26/20  2/27/20  2/28/20  2/29/20  3/1/20  3/2/20  3/3/20  \
Country/Region                                                               
Afghanistan           0        0        0        0       0       0       0   
Albania               0        0        0        0       0       0       0   
Algeria               0        0        0        0       0       0       0   

                3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  3/9/20  3/10/20  \
Country/Region                                                            
Afghanistan          0       0       0       0       0       0        0   
Albania              0       0       0       0       0       0        0   
Algeria              0       0       0       0       0       0        0   

                3/11/20  3/12/20  3/13/20  3/14/20  3/15/20  3/16/20  3/17/20  \
Country/Re

In [113]:
# Checking for the missing values in the Recovered Cases dataset

gr_recovered.isnull().sum().sum()
gr_recovered.isna().sum().sum()

# Hence, there are no missing values in our Recovered Cases data. 

0

##### Shifting all data to one starting point & converting the Dates format to Days
Converting the Dates format to Days to bring all countries data to start from 1 starting point "Day1: 1"
Day1: 1,  is the day on which the confirmed cases for the country got greater than or equal to 10 

In [114]:
# Dates are converted into no of days since 1/1/20 so that 1/1/20 corresponds to day 1
gr_recovered_melt = gr_recovered
dates = gr_recovered_melt.keys()
FMT = '%m/%d/%y'

days = dates.map(lambda x: (datetime.strptime(x, FMT) - datetime.strptime("1/1/20", FMT)).days)

days = days + 1
# +1 is to start the days from 1 instead of 0

gr_recovered_melt.columns = days # = dates will convert the columns to date formats again

x_lag # x_lag gives position of first value in each row which is greater than or equal to 5 in confirmed cases data

for i in range(gr_recovered_melt.shape[0]): # gr_recovered_melt.shape[0] = 187 (no. of rows) and gr_recovered_melt.shape[1] = 138 (no. of columns)
    gr_recovered_melt.iloc[i] = gr_recovered_melt.iloc[i].shift(periods=-x_lag[i]+1) # all data shift to one starting point 
gr_recovered_melt.head(3)

#### Melting our Confirmed Cases dataset

gr_recovered_melt = gr_recovered_melt.reset_index()
gr_recovered_melt = pd.melt(gr_recovered_melt,id_vars= "Country/Region", 
                       value_vars=days, var_name="Days", 
                       value_name="Recovered Cases").sort_values(["Country/Region","Days"])

gr_recovered_melt.set_index("Country/Region", inplace = True)
# gr_recovered_melt.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/Recovered_daywise_melted.csv")
# gr_recovered_melt.shape
gr_recovered_melt.head(5)

Days  Recovered Cases
Country/Region                      
Afghanistan       1              0.0
Afghanistan       2              0.0
Afghanistan       3              1.0
Afghanistan       4              1.0
Afghanistan       5              1.0

#### Importing Dataset for Testing of COVID-19 

In [115]:
url_test= 'https://raw.githubusercontent.com/owid/covid-19-data/master/public/data/testing/covid-testing-all-observations.csv'
df_test = pd.read_csv(url_test)
#                       , index_col="Entity")
# df_test = pd.read_csv("../input/covid19testing-data/public/data/testing/covid-testing-all-observations.csv",
#                       header = 0)
#                       , index_col="Entity")
df_test.head(2)

Entity ISO code        Date  \
0  Argentina - tests performed      ARG  2020-04-08   
1  Argentina - tests performed      ARG  2020-04-09   

                                          Source URL             Source label  \
0  https://www.argentina.gob.ar/sites/default/fil...  Government of Argentina   
1  https://www.argentina.gob.ar/sites/default/fil...  Government of Argentina   

  Notes  Cumulative total  Daily change in cumulative total  \
0   NaN           13330.0                               NaN   
1   NaN           14850.0                            1520.0   

   Cumulative total per thousand  \
0                          0.295   
1                          0.329   

   Daily change in cumulative total per thousand  7-day smoothed daily change  \
0                                            NaN                          NaN   
1                                          0.034                          NaN   

   7-day smoothed daily change per thousand  
0                                       NaN  
1                                       NaN

##### Data Preprocessing for the dataset IV

In [116]:
df_test.shape

(9724, 12)

In [117]:
df_test.columns

Index(['Entity', 'ISO code', 'Date', 'Source URL', 'Source label', 'Notes',
       'Cumulative total', 'Daily change in cumulative total',
       'Cumulative total per thousand',
       'Daily change in cumulative total per thousand',
       '7-day smoothed daily change',
       '7-day smoothed daily change per thousand'],
      dtype='object')

######  Removing the not required columns for the analysis from the testing data

In [118]:
df_test.drop(['Source URL', 'Source label', 'Notes','Daily change in cumulative total',
       'Cumulative total per thousand',
       'Daily change in cumulative total per thousand',
       '7-day smoothed daily change',
       '7-day smoothed daily change per thousand', 'ISO code'], axis=1, inplace=True)

In [119]:
df_test.head(3)

Entity        Date  Cumulative total
0  Argentina - tests performed  2020-04-08           13330.0
1  Argentina - tests performed  2020-04-09           14850.0
2  Argentina - tests performed  2020-04-10           16379.0

######  Changing the "Entity" column to make it more useful for our analysis

In [120]:
# When we groupby on a column it becomes the index for the dataframe. Here we did group_by on "Entity", so it is the index for
# the resuting dataframe now.

# Since here the name of the country column is "Entity", which is different from the name of te country column "Country/Region"
# in confirmed cases and deaths dataset
# Also Since the country names are concatenated with strings "- tests performed" which we need to separate from name of the country 
# names in that string. 
# So to perform both of these functions we choose to change the index column  "Entity" to a normal column and then peform the 
# required changes on it and then after applying the changes we can reset it to index again.

In [121]:
# Do the following:
# a) Change the name of the index column to "Country/Region" as in Confirmed Cases/Deaths and Recovered Cases datasets
# b) Get the country name from the value under Entity column like: "Argentina" from "Argentina - tests performed"

In [122]:
# a) Changing the name of the column

# Modifying the name of the "Entity" column to "Country/Region" as in confirmed and deaths datasets to join them using same 
# column with same name

df_test= df_test.rename(columns={"Entity":"Country/Region", "Cumulative total": "Cumulative_Testing_Count"})
# df_test.columns
df_test.head(3)

Country/Region        Date  Cumulative_Testing_Count
0  Argentina - tests performed  2020-04-08                   13330.0
1  Argentina - tests performed  2020-04-09                   14850.0
2  Argentina - tests performed  2020-04-10                   16379.0

In [123]:
# b) To get the country name from the value under Entity column like: "Argentina" from "Argentina - tests performed"
df_test["Country/Region"]= df_test["Country/Region"].str.split(" -", n=1, expand=True)
df_test.head(3)

Country/Region        Date  Cumulative_Testing_Count
0      Argentina  2020-04-08                   13330.0
1      Argentina  2020-04-09                   14850.0
2      Argentina  2020-04-10                   16379.0


###### Changing the "Date" column from object type to type datetime and then changing it to the format present in Confirmed Cases/ Deaths/Recovered Cases datasets for "Dates"

In [124]:
# type(df_test["Date"])
df_test.dtypes

Country/Region               object
Date                         object
Cumulative_Testing_Count    float64
dtype: object

In [125]:
df_test['Date'] = df_test['Date'].astype('datetime64[ns]')    

df_test.dtypes

Country/Region                      object
Date                        datetime64[ns]
Cumulative_Testing_Count           float64
dtype: object

In [126]:
df_test['Date'] = df_test['Date'].astype('datetime64[ns]')    

# Changing the format of the "Date" column to the one matching the dates in Confirmed Cases/Deaths and Recovered Cases datasets.
df_test['Date'] = df_test['Date'].dt.strftime('%m/%d/%y')
df_test.dtypes

Country/Region               object
Date                         object
Cumulative_Testing_Count    float64
dtype: object

###### Unmelting the Testing data such that the individual dates form the separate columns

In [127]:
df_test_unmelted = df_test.pivot_table(index="Country/Region", columns='Date')
df_test_unmelted = df_test_unmelted["Cumulative_Testing_Count"].reset_index()
df_test_unmelted.columns.name = None
df_test_unmelted_CheckCopyNAN = df_test_unmelted.copy()
# df_test_unmelted_CheckCopyNAN.to_csv("C:/Users/user/Downloads/COVID-19 Related Info/Created Files/df_test_NAN.csv")
df_test_unmelted.head(3)

Country/Region  01/01/20  01/02/20  01/03/20  01/04/20  01/05/20  01/06/20  \
0      Argentina       NaN       NaN       NaN       NaN       NaN       NaN   
1      Australia       NaN       NaN       NaN       NaN       NaN       NaN   
2        Austria       NaN       NaN       NaN       NaN       NaN       NaN   

   01/07/20  01/08/20  01/09/20  01/10/20  01/11/20  01/12/20  01/13/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/14/20  01/15/20  01/16/20  01/17/20  01/18/20  01/19/20  01/20/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/21/20  01/22/20  01/23/20  01/24/20  01/25/20  01/26/20  01/27/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/28/20  01/29/20  01/30/20  01/31/20  02/01/20  02/02/20  02/03/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/04/20  02/05/20  02/06/20  02/07/20  02/08/20  02/09/20  02/10/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/11/20  02/12/20  02/13/20  02/14/20  02/15/20  02/16/20  02/17/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/18/20  02/19/20  02/20/20  02/21/20  02/22/20  02/23/20  02/24/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/25/20  02/26/20  02/27/20  02/28/20  02/29/20  03/01/20  03/02/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2     218.0     321.0     447.0     763.0    1649.0       NaN       NaN   

   03/03/20  03/04/20  03/05/20  03/06/20  03/07/20  03/08/20  03/09/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2    2683.0    3138.0    3711.0    4000.0    4308.0    4509.0    4734.0   

   03/10/20  03/11/20  03/12/20  03/13/20  03/14/20  03/15/20  03/16/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2    5026.0    5362.0    5869.0    6582.0    7467.0    8167.0    8490.0   

   03/17/20  03/18/20  03/19/20  03/20/20  03/21/20  03/22/20  03/23/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN  143056.0       NaN   
2   10278.0   11977.0   13724.0   15613.0   18545.0   21368.0   23429.0   

   03/24/20  03/25/20  03/26/20  03/27/20  03/28/20  03/29/20  03/30/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN  211261.0       NaN   
2   28391.0   32407.0   35995.0   39552.0   42750.0   46441.0   49455.0   

   03/31/20  04/01/20  04/02/20  04/03/20  04/04/20  04/05/20  04/06/

###### Filling Missing values with appropriate values

In [128]:
##### 5a)

# The testing data is not available for all dates for the countries, even after getting first non empty observation for the 
# country for its testing data there are further dates for which no data is available.
# For example for Argentina testing data is available from Apr 8,2020 till present date but is in between missing for some dates
# like April 12, 2020, for Australia first observation on March 22, 2020 but no data till March 28th after that and similarly for 
# other countries. 
# So we will fill those empty values with the previous non-zero values as follows.

# df_test_unmelted.mask(df_test_unmelted.iloc[:, 1:] == 0).ffill(downcast='infer', axis=1, inplace = True)
df_test_unmelted.iloc[:, 1:] = df_test_unmelted.iloc[:, 1:].fillna(method='ffill', downcast='infer', axis=1)
df_test_unmelted.head(3)

Country/Region  01/01/20  01/02/20  01/03/20  01/04/20  01/05/20  01/06/20  \
0      Argentina       NaN       NaN       NaN       NaN       NaN       NaN   
1      Australia       NaN       NaN       NaN       NaN       NaN       NaN   
2        Austria       NaN       NaN       NaN       NaN       NaN       NaN   

   01/07/20  01/08/20  01/09/20  01/10/20  01/11/20  01/12/20  01/13/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/14/20  01/15/20  01/16/20  01/17/20  01/18/20  01/19/20  01/20/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/21/20  01/22/20  01/23/20  01/24/20  01/25/20  01/26/20  01/27/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/28/20  01/29/20  01/30/20  01/31/20  02/01/20  02/02/20  02/03/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/04/20  02/05/20  02/06/20  02/07/20  02/08/20  02/09/20  02/10/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/11/20  02/12/20  02/13/20  02/14/20  02/15/20  02/16/20  02/17/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/18/20  02/19/20  02/20/20  02/21/20  02/22/20  02/23/20  02/24/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/25/20  02/26/20  02/27/20  02/28/20  02/29/20  03/01/20  03/02/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2     218.0     321.0     447.0     763.0    1649.0    1649.0    1649.0   

   03/03/20  03/04/20  03/05/20  03/06/20  03/07/20  03/08/20  03/09/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2    2683.0    3138.0    3711.0    4000.0    4308.0    4509.0    4734.0   

   03/10/20  03/11/20  03/12/20  03/13/20  03/14/20  03/15/20  03/16/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2    5026.0    5362.0    5869.0    6582.0    7467.0    8167.0    8490.0   

   03/17/20  03/18/20  03/19/20  03/20/20  03/21/20  03/22/20  03/23/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN  143056.0  143056.0   
2   10278.0   11977.0   13724.0   15613.0   18545.0   21368.0   23429.0   

   03/24/20  03/25/20  03/26/20  03/27/20  03/28/20  03/29/20  03/30/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1  143056.0  143056.0  143056.0  143056.0  143056.0  211261.0  211261.0   
2   28391.0   32407.0   35995.0   39552.0   42750.0   46441.0   49455.0   

   03/31/20  04/01/20  04/02/20  04/03/20  04/04/20  04/05/20  04/06/

In [129]:
##### 5b)

# Now filling the remaining missing values which are before the first non-zero values for any country with zeroes

df_test_unmelted = df_test_unmelted.fillna(0)
df_test_unmelted.head(3)

Country/Region  01/01/20  01/02/20  01/03/20  01/04/20  01/05/20  01/06/20  \
0      Argentina       0.0       0.0       0.0       0.0       0.0       0.0   
1      Australia       0.0       0.0       0.0       0.0       0.0       0.0   
2        Austria       0.0       0.0       0.0       0.0       0.0       0.0   

   01/07/20  01/08/20  01/09/20  01/10/20  01/11/20  01/12/20  01/13/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   01/14/20  01/15/20  01/16/20  01/17/20  01/18/20  01/19/20  01/20/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   01/21/20  01/22/20  01/23/20  01/24/20  01/25/20  01/26/20  01/27/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   01/28/20  01/29/20  01/30/20  01/31/20  02/01/20  02/02/20  02/03/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   02/04/20  02/05/20  02/06/20  02/07/20  02/08/20  02/09/20  02/10/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   02/11/20  02/12/20  02/13/20  02/14/20  02/15/20  02/16/20  02/17/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   02/18/20  02/19/20  02/20/20  02/21/20  02/22/20  02/23/20  02/24/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

   02/25/20  02/26/20  02/27/20  02/28/20  02/29/20  03/01/20  03/02/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2     218.0     321.0     447.0     763.0    1649.0    1649.0    1649.0   

   03/03/20  03/04/20  03/05/20  03/06/20  03/07/20  03/08/20  03/09/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2    2683.0    3138.0    3711.0    4000.0    4308.0    4509.0    4734.0   

   03/10/20  03/11/20  03/12/20  03/13/20  03/14/20  03/15/20  03/16/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
2    5026.0    5362.0    5869.0    6582.0    7467.0    8167.0    8490.0   

   03/17/20  03/18/20  03/19/20  03/20/20  03/21/20  03/22/20  03/23/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1       0.0       0.0       0.0       0.0       0.0  143056.0  143056.0   
2   10278.0   11977.0   13724.0   15613.0   18545.0   21368.0   23429.0   

   03/24/20  03/25/20  03/26/20  03/27/20  03/28/20  03/29/20  03/30/20  \
0       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
1  143056.0  143056.0  143056.0  143056.0  143056.0  211261.0  211261.0   
2   28391.0   32407.0   35995.0   39552.0   42750.0   46441.0   49455.0   

   03/31/20  04/01/20  04/02/20  04/03/20  04/04/20  04/05/20  04/06/

###### Preparing the testing data to be merged with the "Confirmed Cases"/"Deaths"/"Recovered" Cases datasets by aligning the "Country/Region" column with other datasets 

In [130]:
# Comparing the Confirmed Cases (or/Deaths/ Recovered Cases) dataset with Testing data for different country names for the same
# country or different countries in the two datasets using the gr_confirmed1 file - the datewise dataset copy of confirmed cases
# and the unmelted testing dataset (df_test_unmelted)

countries_in_either_datasets = pd.merge(gr_confirmed1["Country/Region"], df_test_unmelted,  how='outer',on= "Country/Region", indicator = True)
# countries_in_either_datasets

countries_only_in_df_ConfirmedData =countries_in_either_datasets[countries_in_either_datasets['_merge'] == 'left_only']
countries_only_in_df_TestData = countries_in_either_datasets[countries_in_either_datasets['_merge'] == 'right_only']

countries_only_in_df_TestData
# countries_only_in_df_ConfirmedData

Country/Region  01/01/20  01/02/20  01/03/20  01/04/20  01/05/20  \
186  Czech Republic       0.0       0.0       0.0       0.0       0.0   
187       Hong Kong       0.0       0.0       0.0       0.0       0.0   
188         Myanmar       0.0       0.0       0.0       0.0       0.0   
189     South Korea       0.0       0.0       0.0       0.0       0.0   
190          Taiwan       0.0       0.0       0.0       0.0       0.0   
191   United States       0.0       0.0       0.0       0.0       0.0   

     01/06/20  01/07/20  01/08/20  01/09/20  01/10/20  01/11/20  01/12/20  \
186       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
187       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
188       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
189       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
190       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
191       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

     01/13/20  01/14/20  01/15/20  01/16/20  01/17/20  01/18/20  01/19/20  \
186       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
187       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
188       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
189       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
190       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
191       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

     01/20/20  01/21/20  01/22/20  01/23/20  01/24/20  01/25/20  01/26/20  \
186       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
187       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
188       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
189       0.0      11.0      16.0      16.0      25.0      25.0      48.0   
190       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
191       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

     01/27/20  01/28/20  01/29/20  01/30/20  01/31/20  02/01/20  02/02/20  \
186      20.0      28.0      33.0      34.0      37.0      38.0      43.0   
187       0.0       0.0       0.0       0.0    3610.0    3610.0    3610.0   
188       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
189      57.0     187.0     187.0     244.0     244.0     371.0     429.0   
190       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
191       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

     02/03/20  02/04/20  02/05/20  02/06/20  02/07/20  02/08/20  02/09/20  \
186      48.0      53.0      53.0      56.0      62.0      62.0      64.0   
187    3610.0    3610.0    3610.0    3610.0    3610.0    3610.0    3610.0   
188       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
189     429.0     607.0     714.0     885.0    1130.0    1701.0    2340.0   
190       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
191       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

     02/10/20  02/11/20  02/12/20  02/13/20  02/14/20  02/15/20  02/16/20  \
186      72.0      74.0      75.0      76.0      76.0      77.0      78.0   
187    3610.0    3610.0    3610.0    3610.0    3610.0    3610.0    3610.0   
188       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
189    2776.0    3629.0    5074.0    5797.0    6854.0    7519.0    7919.0   
190       0.0       0.0       0.0       0.0       0.0       0.0       0.0   
191       0.0       0.0       0.0       0.0       0.0       0.0       0.0   

     02/17/20  02/18/20  02/19/20  02/20/20  02/21/20  02/22/20  02/23/20  \
186      80.0      80.0      82.0      82.0      82.0      83.0      86.0   
187    3610.0    3610.0    3610.0    3610.0    3610.0    3610.0    3610.0   
188       0.0       0.

In [131]:
# Doing this check we get to know that in gr_death and gr_confirmed and gr_recovered has 186 rows each and all values are common
# but in test_df there are just 82 rows out of which following rows are just in test_df and some values out of these are different 
# names for the same country presnt in the other 3 dataframes. So we rename those values and keep other which are not present
# in other 3 dataframes just like that, with NAs for their columns for those countries.

# gr_confirmed1 = gr_confirmed1.rename(index={'Taiwan*': 'Taiwan'})
# df_test_unmelted = df_test_unmelted.rename(index={'United States': 'US', "Czech Republic":"Czechia", "South Korea": "Korea, South"})

gr_confirmed1["Country/Region"].replace({'Taiwan*': 'Taiwan'}, inplace = True)
df_test_unmelted["Country/Region"].replace({'United States': 'US', "Czech Republic":"Czechia", "South Korea": "Korea, South", "Myanmar": "Burma"}, inplace = True)


In [132]:
# Making the Changes in original datasets of Confirmed Cases/ Deaths/ Recovered  datasets and their melted forms

gr_confirmed = gr_confirmed.rename(index={'Taiwan*': 'Taiwan'})
gr_death = gr_death.rename(index={'Taiwan*': 'Taiwan'})
gr_recovered = gr_recovered.rename(index={'Taiwan*': 'Taiwan'})

gr_confirmed_melt = gr_confirmed_melt.rename(index={'Taiwan*': 'Taiwan'})
gr_death_melt = gr_death_melt.rename(index={'Taiwan*': 'Taiwan'})
gr_recovered_melt = gr_recovered_melt.rename(index={'Taiwan*': 'Taiwan'})

In [133]:
# Since there are just 2 countries namely "Czech Republic" and "Hong Kong"  which are "only" in Testing data and all 
# the other "Country/Region" value in testing data are there in Confirmed/Deaths/Recovered cases datasets.

# So we leave these three countries for the purpose of analysis and keep only the "Country/Region" values which are in 
# both datasets (Confirmed/Deaths/Recovered cases dataset and Testing dataset) 

In [134]:
# To include all the countries which are there in Confirmed Cases/ Deaths/ Recovered Cases Datasets 
# By joining the "Country/Region"  column in Confirmed Cases dataset with the whole testing (unmelted) data by joining on
# common column "Country/Region"

# df_test_unmelted = pd.merge(gr_confirmed1['Country/Region'], df_test_unmelted, on='Country/Region', how='outer', indicator=True)
# df_test_unmelted = df_test_unmelted_1[df_test_unmelted_1['_merge'] == 'left_only']
df_test_unmelted = pd.merge(gr_confirmed1['Country/Region'], df_test_unmelted, on='Country/Region', how='left')
df_test_unmelted.head(3)

Country/Region  01/01/20  01/02/20  01/03/20  01/04/20  01/05/20  01/06/20  \
0    Afghanistan       NaN       NaN       NaN       NaN       NaN       NaN   
1        Albania       NaN       NaN       NaN       NaN       NaN       NaN   
2        Algeria       NaN       NaN       NaN       NaN       NaN       NaN   

   01/07/20  01/08/20  01/09/20  01/10/20  01/11/20  01/12/20  01/13/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/14/20  01/15/20  01/16/20  01/17/20  01/18/20  01/19/20  01/20/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/21/20  01/22/20  01/23/20  01/24/20  01/25/20  01/26/20  01/27/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   01/28/20  01/29/20  01/30/20  01/31/20  02/01/20  02/02/20  02/03/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/04/20  02/05/20  02/06/20  02/07/20  02/08/20  02/09/20  02/10/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/11/20  02/12/20  02/13/20  02/14/20  02/15/20  02/16/20  02/17/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/18/20  02/19/20  02/20/20  02/21/20  02/22/20  02/23/20  02/24/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   02/25/20  02/26/20  02/27/20  02/28/20  02/29/20  03/01/20  03/02/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   03/03/20  03/04/20  03/05/20  03/06/20  03/07/20  03/08/20  03/09/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   03/10/20  03/11/20  03/12/20  03/13/20  03/14/20  03/15/20  03/16/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   03/17/20  03/18/20  03/19/20  03/20/20  03/21/20  03/22/20  03/23/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   03/24/20  03/25/20  03/26/20  03/27/20  03/28/20  03/29/20  03/30/20  \
0       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
2       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

   03/31/20  04/01/20  04/02/20  04/03/20  04/04/20  04/05/20  04/06/

In [135]:
# Filling the missing values in the rows("Country/Region" values) which were earlier only in Confirmed/Deaths/Recovered Datasets
# but now after merging the "Country/Region" column in Confirmed Cases dataset, are there in testing data also with 0.

In [136]:
df_test_unmelted.fillna(0, inplace=True)
df_test_unmelted.set_index("Country/Region", inplace=True)
# df_test_unmelted.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/Testing_datewise.csv")
df_test_unmelted.head(3)

01/01/20  01/02/20  01/03/20  01/04/20  01/05/20  01/06/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                01/07/20  01/08/20  01/09/20  01/10/20  01/11/20  01/12/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                01/13/20  01/14/20  01/15/20  01/16/20  01/17/20  01/18/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                01/19/20  01/20/20  01/21/20  01/22/20  01/23/20  01/24/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                01/25/20  01/26/20  01/27/20  01/28/20  01/29/20  01/30/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                01/31/20  02/01/20  02/02/20  02/03/20  02/04/20  02/05/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                02/06/20  02/07/20  02/08/20  02/09/20  02/10/20  02/11/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                02/12/20  02/13/20  02/14/20  02/15/20  02/16/20  02/17/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                02/18/20  02/19/20  02/20/20  02/21/20  02/22/20  02/23/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                02/24/20  02/25/20  02/26/20  02/27/20  02/28/20  02/29/20  \
Country/Region                                                               
Afghanistan          0.0       0.0       0.0       0.0       0.0       0.0   
Albania              0.0       0.0       0.0       0.0       0.0       0.0   
Algeria              0.0       0.0       0.0       0.0       0.0       0.0   

                03/01/20  03/02/20  03/03/20  03/04/20  03/05/20  03/06/20  \
Country/Region              

In [137]:
df_test_unmelted1 = df_test_unmelted.copy()
df_test_unmelted.info()

<class 'pandas.core.frame.DataFrame'>
Index: 186 entries, Afghanistan to Zimbabwe
Columns: 180 entries, 01/01/20 to 06/28/20
dtypes: float64(180)
memory usage: 263.0+ KB


##### Shifting all data to one starting point & converting the Dates format to Days 
Converting the Dates format to Days to bring all countries data to start from 1 starting point "Day1: 1"
Day1: 1,  is the day on which the confirmed cases for the country got greater than or equal to 10 

In [138]:
# Dates are converted into no of days since 1/1/20 so that 1/1/20 corresponds to day 1
df_test_melt = df_test_unmelted
dates = df_test_melt.keys()
FMT = '%m/%d/%y'

days = dates.map(lambda x: (datetime.strptime(x, FMT) - datetime.strptime("01/01/20", FMT)).days)
days = days + 1
# +1 is to start the days from 1 instead of 0

df_test_melt.columns = days # = dates will convert the columns to date formats again

x_lag  # x_lag gives position of first value in each row which is greater than or equal to 5 in confirmed cases data

for i in range(df_test_melt.shape[0]): # gr_recovered_melt.shape[0] = 187 (no. of rows) and gr_recovered_melt.shape[1] = 138 (no. of columns)
    df_test_melt.iloc[i] = df_test_melt.iloc[i].shift(periods=-x_lag[i]+1) # all data shift to one starting point 
df_test_melt.head(3)

#### Melting our Confirmed Cases dataset

df_test_melt = df_test_melt.reset_index()
df_test_melt = pd.melt(df_test_melt,id_vars= "Country/Region", 
                       value_vars=days, var_name="Days", 
                       value_name="Testing Count").sort_values(["Country/Region","Days"])

# df_test_melt.columns = dates
df_test_melt.set_index("Country/Region", inplace = True)
# df_test_melt.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/Testing_daywise_melted.csv")
# df_test_melt.shape
df_test_melt.head(3)

Days  Testing Count
Country/Region                    
Afghanistan       1            0.0
Afghanistan       2            0.0
Afghanistan       3            0.0

### Merging the 4 datasets: 
#### confirmed, deaths, recovered, and testing

In [139]:
# gr_confirmed_melt.shape
# gr_death_melt.shape
# gr_recovered_melt.shape
# gr_recovered_melt.shape
# df_test_melt.shape

In [140]:
df1 = gr_confirmed_melt.reset_index()
df2 = gr_death_melt.reset_index()
df3 = gr_recovered_melt.reset_index()
df4 = df_test_melt.reset_index()

In [141]:
# df1.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/df1.csv")
# df2.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/df2.csv")
# df3.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/df3.csv")
# df4.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/df4.csv")

In [142]:
data = [df1, df2, df3, df4]
len(data)
for i in range(1,(len(data))): # Actually the loop runs for len(data)-1 time, because upper bound is not included
    data[0] = pd.merge(data[0], data[i], how="inner", on=["Country/Region", "Days"])
MergedData = data[0]
# MergedData.set_index("Country/Region", inplace = True)

In [143]:
# MergedData.to_csv("C:/Users/user/Downloads/COVID-19 Related info/Created Files/Merged_Data.csv")

In [144]:
MergedData.head()

Country/Region Days  Confirmed Cases  Deaths  Recovered Cases  Testing Count
0    Afghanistan    1             11.0     0.0              0.0            0.0
1    Afghanistan    2             16.0     0.0              0.0            0.0
2    Afghanistan    3             21.0     0.0              1.0            0.0
3    Afghanistan    4             22.0     0.0              1.0            0.0
4    Afghanistan    5             22.0     0.0              1.0            0.0

In [145]:
MergedData.isna().sum()

Country/Region         0
Days                   0
Confirmed Cases    14384
Deaths             14384
Recovered Cases    14384
Testing Count      14384
dtype: int64

<b><i> All these NaNs are the empty values for the individual countries after the current day for their Confirmed/Deaths/Recovered/Testing data: Every Country has different value for current day number based on when did they get the 10 or more confirmed cases which is set as day 1 for it. Since these are empty values we drop them with no loss of information. </i></b>

In [146]:
# MergedData = MergedData.dropna()
MergedData.isna().sum()

Country/Region         0
Days                   0
Confirmed Cases    14384
Deaths             14384
Recovered Cases    14384
Testing Count      14384
dtype: int64

### Adding more information to Merged data

#### Adding Population and Population density information for each country : https://www.worldometers.info/world-population/population-by-country/

##### Reading population data

In [147]:
# path = "C:\Users\user\Downloads\COVID-19 Related info"
df_pop = pd.read_csv("C:/Users/user/Downloads/COVID-19 Related info/Population Data.csv", encoding  = 'latin-1')
df_pop.head(3)

Country/Region  Population  Pop_Density  Land_Area_Kmsq
0    Afghanistan    38928346           60          652860
1        Albania     2877797          105           27400
2        Algeria    43851044           18         2381740

In [148]:
df_pop.shape

(235, 4)

##### Data Cleaning: To match country names  in population data with the country names in our created MergedData above so that we can join them properly

In [149]:
m = pd.merge(MergedData, df_pop, how="outer", on=["Country/Region"], indicator = True)

In [150]:
# Check which countries are only in df_pop and which are only in MergedData and see if there are different names 
# for the same countries in the two dataframes and naming them identically

# m[m['_merge'] == 'right_only']
# m[m['_merge'] == 'left_only']

In [151]:
# df_pop - MergedData
# Myanmar - Burma
# Congo - Congo (Brazzaville)
# DR Congo - Congo (Kinshasa)
# Côte d'Ivoire - Cote d'Ivoire
# Czech Republic (Czechia) - Czechia
# South Korea - Korea, South
#    ? - Kosovo
# Saint Kitts & Nevis- Saint Kitts and Nevis
# St. Vincent & Grenadines - Saint Vincent and the Grenadines
# Sao Tome & Principe - Sao Tome and Principe
# United States - US
# State of Palestine - West Bank and Gaza	

df_pop['Country/Region'] = df_pop['Country/Region'].replace({ 'Myanmar': 'Burma',
                                                               'Congo': 'Congo (Brazzaville)',
                                                               'DR Congo': 'Congo (Kinshasa)',
                                                               'Côte d\'Ivoire': 'Cote d\'Ivoire',
                                                               'Czech Republic (Czechia)': 'Czechia',
                                                              'South Korea': 'Korea, South',
                                                              'Saint Kitts & Nevis':'Saint Kitts and Nevis',
                                                              'St. Vincent & Grenadines':'Saint Vincent and the Grenadines',
                                                              'Sao Tome & Principe':'Sao Tome and Principe',
                                                              'United States': 'US',
                                                              'State of Palestine' : 'West Bank and Gaza',
                                                              })


##### Now merging the cleaned population data (df_pop) with the MergedData: Keeping only the countries which are in MergedData (Covid Data)

In [152]:
MergedData = pd.merge(MergedData, df_pop, how="left", on=["Country/Region"])
MergedData.head(3)

Country/Region Days  Confirmed Cases  Deaths  Recovered Cases  \
0    Afghanistan    1             11.0     0.0              0.0   
1    Afghanistan    2             16.0     0.0              0.0   
2    Afghanistan    3             21.0     0.0              1.0   

   Testing Count  Population  Pop_Density  Land_Area_Kmsq  
0            0.0  38928346.0         60.0        652860.0  
1            0.0  38928346.0         60.0        652860.0  
2            0.0  38928346.0         60.0        652860.0

In [153]:
MergedData.head()

Country/Region Days  Confirmed Cases  Deaths  Recovered Cases  \
0    Afghanistan    1             11.0     0.0              0.0   
1    Afghanistan    2             16.0     0.0              0.0   
2    Afghanistan    3             21.0     0.0              1.0   
3    Afghanistan    4             22.0     0.0              1.0   
4    Afghanistan    5             22.0     0.0              1.0   

   Testing Count  Population  Pop_Density  Land_Area_Kmsq  
0            0.0  38928346.0         60.0        652860.0  
1            0.0  38928346.0         60.0        652860.0  
2            0.0  38928346.0         60.0        652860.0  
3            0.0  38928346.0         60.0        652860.0  
4            0.0  38928346.0         60.0        652860.0

#### Adding Active Cases, Recovery Rate and Testing Rate to the MergedData by deriving them from the available columns in the dataframe 

In [154]:
MergedData.columns

Index(['Country/Region', 'Days', 'Confirmed Cases', 'Deaths',
       'Recovered Cases', 'Testing Count', 'Population', 'Pop_Density',
       'Land_Area_Kmsq'],
      dtype='object')

In [155]:
MergedData["RecoveryRate"] = round(MergedData["Recovered Cases"]/MergedData["Confirmed Cases"],2)
MergedData["ActiveCases"] = MergedData["Confirmed Cases"]-MergedData["Recovered Cases"]-MergedData["Deaths"]
MergedData["TestingRate"] = round(MergedData["Testing Count"]/MergedData["Population"],2)

In [156]:
MergedData.head(3)

Country/Region Days  Confirmed Cases  Deaths  Recovered Cases  \
0    Afghanistan    1             11.0     0.0              0.0   
1    Afghanistan    2             16.0     0.0              0.0   
2    Afghanistan    3             21.0     0.0              1.0   

   Testing Count  Population  Pop_Density  Land_Area_Kmsq  RecoveryRate  \
0            0.0  38928346.0         60.0        652860.0          0.00   
1            0.0  38928346.0         60.0        652860.0          0.00   
2            0.0  38928346.0         60.0        652860.0          0.05   

   ActiveCases  TestingRate  
0         11.0          0.0  
1         16.0          0.0  
2         20.0          0.0

> ### Visualization

<b> Importing related libraries </b>

In [54]:
#output_file-to save the layout in file, show-display the layout , output_notebook-to configure the default output state  to generate the output in jupytor notebook.
from bokeh.io import output_file, show, output_notebook 
#ColumnDataSource makes selection of the column easier and Select is used to create drop down 
from bokeh.models import ColumnDataSource, DataRange1d, Legend, Select, RadioGroup, MultiSelect
#Figure objects have many glyph methods that can be used to draw vectorized graphical glyphs. example of glyphs-circle, line, scattter etc. 
from bokeh.plotting import figure 
#To create intractive plot we need this to add callback method.
from bokeh.models import CustomJS, Panel, Tabs, BoxAnnotation
#This is for creating layout
from bokeh.layouts import column, row, gridplot
from bokeh.models import ZoomInTool,ZoomOutTool, ResetTool, HoverTool, BoxZoomTool
from bokeh.io import curdoc
from bokeh.layouts import layout
from bokeh.palettes import YlOrRd, RdYlGn, Inferno, Viridis, Magma
output_notebook() #create default state to generate the output


Loading BokehJS ...

#### Visualization 1: Confirmed, Recovered, Deaths, Testing Vs. Days for all Countries

##### Preparing Data

In [55]:
data = MergedData.copy()
# data = data.reset_index()
# data.head()

In [56]:
# Spaced column names donot returend values while hovering over bokeh plot, so creating one word 
# names for columns

data.rename(columns={'Country/Region': 'Country','Confirmed Cases':'Confirmed',
                          'Recovered Cases':'Recovered',
                          'Testing Count':'Testing', 
                    'ActiveCases': 'Active'}, 
                 inplace=True)
# data[data["Country"] == "Sweden"].head()

##### Plotting

In [57]:
# Preparing ColumnDataSources from data_all

data_all=data.loc[:, ['Country','Days', 'Confirmed', 'Deaths', 'Recovered', 'Testing']]
data_curr = data_all[data_all['Country'] == 'Afghanistan' ]

Overall = ColumnDataSource(data=data_all)
Curr=ColumnDataSource(data=data_curr)

# Creating plots

#------------------------------------------------------------------------------------------


# Linking plots to be created with the menu of countries
# plots and the menu is linked with each other by this callback function

callback = CustomJS(args=dict(source=Overall, current=Curr), code="""
var selected_country = cb_obj.value
current.data['Days']=[]
current.data['Confirmed']=[]
current.data['Deaths'] = []
current.data['Recovered'] = []
current.data['Testing'] = []
for(var i = 0; i <= source.get_length(); i++){
	if (source.data['Country'][i] == selected_country){
		current.data['Days'].push(source.data['Days'][i])
		current.data['Confirmed'].push(source.data['Confirmed'][i])
		current.data['Deaths'].push(source.data['Deaths'][i])
		current.data['Recovered'].push(source.data['Recovered'][i])
		current.data['Testing'].push(source.data['Testing'][i]) 
	 }          
} 
current.change.emit();
""")

#-------------------------------------------------------------------------------------------

# A) Creating menu

menu = Select(options=list(data['Country'].unique()),value='Afghanistan', title="Country/Region")  # drop down menu
# menu.js_on_change('value', callback)
#------------------------------------------------------------------------------------------

# B) Creating plot

# Step 1
# Creating empty list for storing two figures :1 with LogScale for y-axis and other with LinearScale
# These two plots are shown in separate tabs in he same plot
P = [] 
axis_type =["log", "linear"]

# Step 2
# Creating figure for the plot
for i in range(2):
    p = figure(x_axis_label ='Days since first 10 confirmed cases', y_axis_label = 'Number of Cases', y_axis_type = axis_type[i])#creating figure object 

# Step 3
# Plotting line graph on the figure
        #    We can use loop to create all the line plots as below. But we want to put each line graph in separate variable to define its
        #    legend later using Legend(). And that is needed to be able to put the legeds outside the plot area. 

      # (i) Using for loop and defining lagend labels alongwith
        #     wanted_keys = ['Confirmed', 'Deaths', 'Recovered', 'Testing']
        #     j= 0 # index for setting colors for different columns (confirmed, deaths, recovered, testing)
        #     mypalette=["red", "black", "darkgreen", "navy"]
        #     for i in wanted_keys:
        #         p.line(x='Days', y=i, source=Curr, color = mypalette[j], legend_label = i.title(), line_width = 2) # plotting the data using glyph circle
        #     #     p.circle(x='Days', y=i, source=Curr, color = mypalette[j], legend_label = i.title()) # plotting the data using glyph circle
        #         j=j+1
    
     # (ii) Storing all line plots in separae variables and defining their legends later under "Define and Stylize" legend block, to
     # be able to put the legends outside the plot area
    line1 = p.line(x='Days', y="Confirmed", source=Curr, color = "red", line_width = 2) # plotting the data using glyph circle
    line2 = p.line(x='Days', y="Deaths", source=Curr, color = "black", line_width = 2)
    line3 = p.line(x='Days', y="Recovered", source=Curr, color = "darkgreen", line_width = 2)
    line4 = p.line(x='Days', y="Testing", source=Curr, color = "navy", line_width = 2)
    #     p.circle(x='Days', y=i, source=Curr, color = mypalette[j], legend_label = i.title()) # plotting the data using glyph circle
    
    
    
    # Stylize the plot area
    p.plot_width = 700                # To change the width of the plot
    p.plot_height = 350                 # To change the height of plot
    p.background_fill_color = "#1f77b4"   # To add background colorto the figure
    p.background_fill_alpha = 0.12
    
    # Stylize the grid
    p.xgrid.grid_line_color = "white"
    p.ygrid.grid_line_color = "white"
    p.ygrid.grid_line_alpha = 0.7
    p.grid.grid_line_dash = [5,3]
    
    # Axes Geometry
    p.x_range = DataRange1d(only_visible=True) # x_range changes according to the active legends
    p.y_range = DataRange1d(only_visible=True) # y_range changes according to the active legends
    
    # Stylize the axes
    p.axis.axis_label_text_font_style = "bold" #"normal", "italic"
    p.axis.axis_label_text_color = "black"
    # p.axis.major_label_text_font_style = "bold" # for axis' major tick marks' labels value color
    p.yaxis.minor_tick_in = 0
    p.yaxis.minor_tick_out = 0
    p.xaxis.minor_tick_in = 0
    p.xaxis.minor_tick_out = 0

    # Stylize the figure title
    p.title.text_color = "black"
    p.title.text_font = "times"
    p.title.text_font_size = "20px" # px stands for pixel. Have to mention.
    p.title.align = "center"

    # Stylize the tools
    # Adding customizayion to HoverTool
    p.tools = [ZoomInTool(),ZoomOutTool(), ResetTool()]
    hover = HoverTool(tooltips = [(("Day", "@Days")),("Confirmed Cases", "@Confirmed"), ("Deaths", "@Deaths"), ("Recovered", "@Recovered"), ("Testing Count", "@Testing")])
    p.add_tools(hover) # Customization of HoverTool
    
    # Stylize the legends
    legend = Legend(items=[
    ("Confirmed Cases",   [line1]),
    ("Deaths", [line2]),
    ("Recovered Cases", [line3]),
    ("Testing Count ",[line4]),    
     ]) #, location=(10,80))
    legend.background_fill_color = "#1f77b4"
    legend.background_fill_alpha = 0.01
    legend.label_text_font = "times"
    legend.label_text_font_size = '12px'
    legend.click_policy="hide"  # To disable/hide the legend on click
    
    # Adding the legends as a layout to the figure
    p.add_layout(legend, 'right')
    
    # Appending the two figures created under for loop, one with y_axis_type="log" and other
    # with y_axis_type = "linear" into list P
    P.append(p)
    
#------------------------------------------------------------------------------------------
# Creating separate tabs for the two figures created above
tab1 = Panel(child=P[0], title="Log scale")
tab2 = Panel(child=P[1], title="Linear scale")

# Creating list of Tabs
tabs = Tabs(tabs=[ tab1, tab2 ])

#------------------------------------------------------------------------------------------

# Calling the function on change of selection

menu.js_on_change('value', callback) 

#------------------------------------------------------------------------------------------

# Creating the layout

layout=column(menu,tabs) 

#------------------------------------------------------------------------------------------
# Displaying the layout
show(layout) 


#### Visualization 2: Recovery Rate and Testing Rate over the period of days since first 10 confirmed cases in the country

In [58]:
# Creating ColumnDataSources from the data_all

data_all=data.loc[:, ['Country','Days', 'Confirmed', 'Recovered', 'Deaths', 'Active', 'Testing', 'RecoveryRate', 'TestingRate', "Population", "Pop_Density"]]

Overall = ColumnDataSource(data=data_all)
Curr = ColumnDataSource(dict(Country = [], Days = [], Confirmed = [], Recovered = [], Deaths = [], Active = [], Testing = [], RecoveryRate = [], TestingRate = [], Population = [], Pop_Density = []))

##### Plotting

##### Creating menu and interation between menu and plots below </b>

#------------------------------------------------------------------------------------------

# Linking plot and menu
# Plot and the menu is linked with each other by this callback function

multi_countries_callback = CustomJS(args=dict(source=Overall, current=Curr), code="""
var Selected_Country = cb_obj.value

current.data['Country'] = []
current.data['Days']=[]
current.data['Confirmed'] = []
current.data['Recovered'] = []
current.data['Deaths'] = []
current.data['Active'] = []
current.data['Testing'] = []
current.data['RecoveryRate'] = []
current.data['TestingRate'] = []
current.data['Population'] = []
current.data['Pop_Density'] = []


for(var i = 0; i <= source.get_length(); i++){
	if (Selected_Country.indexOf(source.data['Country'][i]) >= 0){
        current.data['Country'].push(source.data['Country'][i])
		current.data['Days'].push(source.data['Days'][i])
        current.data['Confirmed'].push(source.data['Confirmed'][i])
        current.data['Recovered'].push(source.data['Recovered'][i])
        current.data['Deaths'].push(source.data['Deaths'][i])
        current.data['Active'].push(source.data['Active'][i])
        current.data['Testing'].push(source.data['Testing'][i])
		current.data['RecoveryRate'].push(source.data['RecoveryRate'][i])
        current.data['TestingRate'].push(source.data['TestingRate'][i])
        current.data['Population'].push(source.data['Population'][i])
        current.data['Pop_Density'].push(source.data['Pop_Density'][i])
        
	 }          
} 
current.change.emit();
""")

#-------------------------------------------------------------------------------------------

# A) Creating menu

menu = MultiSelect(options=list(data['Country'].unique()),value=[], title="Country/Region")  # drop down menu


#### Plots

#------------------------------------------------------------------------------------------
# B)i) Creating plots


# Step 1
# Creating figure for the plot
plots = []

y = ["RecoveryRate", "TestingRate"]

for y in y: 
    p1 = figure(x_axis_label ='Days since first 10 confirmed cases', y_axis_label = y, y_axis_type ="linear")#creating figure object 

# Step 2
# Creating the graph on figure
    line = p1.line(x='Days', y= y, source=Curr, color = "black", line_width = 2, legend_label = y) # plotting the data using glyph circle
    #     p.circle(x='Days', y=i, source=Curr, color = mypalette[j], legend_label = i.title()) # plotting the data using glyph circle


    # Stylize the plot area
    p1.plot_width = 400                # To change the width of the plot
    p1.plot_height = 350                 # To change the height of plot
    # p.background_fill_color = "#1f77b4"   # To add background colorto the figure
    # p.background_fill_alpha = 0.12

    # Stylize the grid
    p1.xgrid.grid_line_color = "white"
    p1.ygrid.grid_line_color = "white"
    p1.ygrid.grid_line_alpha = 0.7
    p1.grid.grid_line_dash = [5,3]

    # Axes Geometry
    # p1.x_range = DataRange1d(only_visible=True) # x_range changes according to the active legends
    # p1.y_range = DataRange1d(only_visible=True) # y_range changes according to the active legends

    # Stylize the axes
    p1.axis.axis_label_text_font_style = "bold" #"normal", "italic"
    p1.axis.axis_label_text_color = "black"
    # p1.axis.major_label_text_font_style = "bold" # for axis' major tick marks' labels value color
    p1.yaxis.minor_tick_in = 0
    p1.yaxis.minor_tick_out = 0
    p1.xaxis.minor_tick_in = 0
    p1.xaxis.minor_tick_out = 0


    # Box Annotations
    verylow_box = BoxAnnotation(bottom = 0, top= 0.25, fill_color=RdYlGn[11][9])
    low_box = BoxAnnotation(bottom=0.25, top=0.50, fill_color=RdYlGn[11][6])
    medium_box = BoxAnnotation(bottom=0.50, top=0.75, fill_color=RdYlGn[11][6])
    high_box = BoxAnnotation(bottom=0.75,top = 1, fill_color=RdYlGn[11][3]) # fill_alpha=0.18,

    p1.add_layout(verylow_box)
    p1.add_layout(low_box)
    p1.add_layout(medium_box)
    p1.add_layout(high_box)


    # Stylize the figure title
    p1.y_range.start = 0
    p1.title.text_color = "black"
    p1.title.text_font = "times"
    p1.title.text_font_size = "20px" # px stands for pixel. Have to mention.
    p1.title.align = "center"

    # Stylize the tools
    # Adding customizayion to HoverTool
    p1.tools = [ZoomInTool(),ZoomOutTool(), ResetTool()]
    hover = HoverTool(tooltips = [("Country", "@Country"),("Day", "@Days"),("Confirmed Cases", "@Confirmed"),("Testing Count", "@Testing"), ("Testing Rate", "@TestingRate{0.00}"), ("Recovered Cases", "@Recovered"),("Recovery Rate", "@RecoveryRate{0.00}")])

    p1.add_tools(hover) # Customization of HoverTool

    # Stylize the legends
    p1.legend.location = "top_center"
    # p1.legend.background_fill_color = "#1f77b4"
    p1.legend.background_fill_alpha = 0
    p1.legend.border_line_color = None
    p1.legend.label_text_font = "times"
    p1.legend.label_text_font_size = '13px'
    
    # Appending the two plots created under for loop, one with y=RecoveryRate and other
    # with y=TestingRate into list plots
    plots.append(p1)

#------------------------------------------------------------------------------------------

# Calling the function on change of selection

menu.js_on_change('value', multi_countries_callback) 

#------------------------------------------------------------------------------------------

# Creating the layout

layout1=column(menu,row(plots[0], plots[1])) 

#------------------------------------------------------------------------------------------
# Displaying the layout
show(layout1) 


#### Visualization 3: Confirmed Cases Vs. Population and Population Density for all countries grouped over defined Testing Rate intervals

##### Preparing Data

<b> Creating present date data for all countries </b>

Creating the dataframe for the current day cases (starting from day 1 which is the day on which that country got its first 10 or more COVID19 cases) for all countries by only taking the last value for their data (i.e. the data for the current date for them) 


Since not all countries have same number of days for their present day cases. So after the current day data for the country there are null values for the following days. Like for Afghanistan if the current date is 101th day since the first 10 COVID19 cases were registered but on current date US is as far as 175th day since first 10 COVID19 cases were registered, so in that case Afghanistan after 101th day has null values for all remaining days till 175 (or till the days for countries with maximum number of days since first 10 COVID19 cases were registerd in that country).

But to go ahead with the next visualization the data for the current day for all countries is needed and that is easy to extract if the null values are dropped. Because then last tail value for every country gives their present day values for Conformed, Recovered, Deaths and Testing 

So we drop null values as follows:

In [59]:
MergedData.isna().sum()

Country/Region         0
Days                   0
Confirmed Cases    14384
Deaths             14384
Recovered Cases    14384
Testing Count      14384
Population           177
Pop_Density          177
Land_Area_Kmsq       177
RecoveryRate       14384
ActiveCases        14384
TestingRate        14476
dtype: int64

<b><i> All these NaNs are the empty values for the individual countries after the current day for their Confirmed/Deaths/Recovered/Testing data: Every Country has different value for current day number based on when did they get the 10 or more confirmed cases which is set as day 1 for it. Since these are empty values we drop them with no loss of information. </i></b>

In [60]:
MergedData = MergedData.dropna()
MergedData.isna().sum()

Country/Region     0
Days               0
Confirmed Cases    0
Deaths             0
Recovered Cases    0
Testing Count      0
Population         0
Pop_Density        0
Land_Area_Kmsq     0
RecoveryRate       0
ActiveCases        0
TestingRate        0
dtype: int64

<b> Getting the present date data for all the countries by accessing the last tail value for each country: </b>

In [61]:
df_tails = pd.DataFrame()
for i in MergedData["Country/Region"].unique():
    df_tails = df_tails.append(MergedData[MergedData["Country/Region"]==i].tail(1))

df_tails = df_tails.reset_index(drop = True)

In [62]:
df_tails.rename(columns={'Country/Region': 'Country','Confirmed Cases':'Confirmed',
                          'Recovered Cases':'Recovered',
                          'Testing Count':'Testing', 
                    'ActiveCases': 'Active'}, 
                 inplace=True)
df_tails.head()

Country Days  Confirmed  Deaths  Recovered  Testing  Population  \
0  Afghanistan  104    30175.0   675.0    10174.0      0.0  38928346.0   
1      Albania  108     2192.0    49.0     1250.0      0.0   2877797.0   
2      Algeria  114    12445.0   878.0     8920.0      0.0  43851044.0   
3      Andorra  101      855.0    52.0      797.0      0.0     77265.0   
4       Angola   83      212.0    10.0       81.0      0.0  32866272.0   

   Pop_Density  Land_Area_Kmsq  RecoveryRate   Active  TestingRate  
0         60.0        652860.0          0.34  19326.0          0.0  
1        105.0         27400.0          0.57    893.0          0.0  
2         18.0       2381740.0          0.72   2647.0          0.0  
3        164.0           470.0          0.93      6.0          0.0  
4         26.0       1246700.0          0.38    121.0          0.0

<b> Creating column containing Intervals for Testing Rate: </b>

In [63]:
def func(x):
    if x == 0:
        return 'Zero Testing'
    if 0 < x < 0.05:
        return '(0% - 5%]'
    if 0.05 <= x < 0.1 :
        return '(5% - 10%]'
    if 0.1 <= x < 0.15:
        return '(10% - 15%]'
    if 0.15 <= x < 0.20:
        return '(15% - 20%]'
    if x >= 0.20:
        return '(20% and more)'
    

df_tails['TestingRateInterval'] = df_tails['TestingRate'].apply(func)

In [64]:
df_tails.head()

Country Days  Confirmed  Deaths  Recovered  Testing  Population  \
0  Afghanistan  104    30175.0   675.0    10174.0      0.0  38928346.0   
1      Albania  108     2192.0    49.0     1250.0      0.0   2877797.0   
2      Algeria  114    12445.0   878.0     8920.0      0.0  43851044.0   
3      Andorra  101      855.0    52.0      797.0      0.0     77265.0   
4       Angola   83      212.0    10.0       81.0      0.0  32866272.0   

   Pop_Density  Land_Area_Kmsq  RecoveryRate   Active  TestingRate  \
0         60.0        652860.0          0.34  19326.0          0.0   
1        105.0         27400.0          0.57    893.0          0.0   
2         18.0       2381740.0          0.72   2647.0          0.0   
3        164.0           470.0          0.93      6.0          0.0   
4         26.0       1246700.0          0.38    121.0          0.0   

  TestingRateInterval  
0        Zero Testing  
1        Zero Testing  
2        Zero Testing  
3        Zero Testing  
4        Zero Testing

In [65]:
# Creating ColumnDataSource from df_tails
df = ColumnDataSource(df_tails)

from bokeh.transform import factor_cmap, factor_mark
from bokeh.models import LinearColorMapper, BasicTicker, ColorBar

# Creating colormap for different levels of testing rate
colormap = {'Zero Testing':"silver",'(0% - 5%]':"wheat", '(5% - 10%]':"yellow",'(10% - 15%]':"orange",'(15% - 20%]':"red", '(20% and more)': "green" } # Giving names to colors
# Creating color column using list comprehension
df_tails["TestingColor"] = [colormap[x] for x in df_tails["TestingRateInterval"]]

plots = [] 
x_list = ["Population", "Pop_Density"]

for x in x_list:
    # Creating the figure
    p3 = figure(x_axis_label = x , y_axis_label = 'Confirmed Cases', y_axis_type ="log",x_axis_type ="log", title =('Confirmed Cases Vs. ' + x + ' for the Countries grouped by their Testing Rate Intervals') ) #creating figure object 

    # Plotting the graph


    c0 = p3.circle(x=x, y = "Confirmed", size =10, fill_alpha = 0.7, color ="TestingColor",line_dash = [3,3], 
                   source = ColumnDataSource(df_tails[df_tails["TestingRateInterval"]=="Zero Testing"]))
    c1 = p3.circle(x=x, y = "Confirmed", size =10, fill_alpha = 0.7, color ="TestingColor",line_dash = [3,3], 
                   source = ColumnDataSource(df_tails[df_tails["TestingRateInterval"]=='(0% - 5%]']))
    c2 = p3.circle(x=x, y = "Confirmed", size =10, fill_alpha = 0.7, color ="TestingColor",line_dash = [3,3], 
                   source = ColumnDataSource(df_tails[df_tails["TestingRateInterval"]=='(5% - 10%]']))
    c3 = p3.circle(x=x, y = "Confirmed", size =10, fill_alpha = 0.7, color ="TestingColor",line_dash = [3,3], 
                   source = ColumnDataSource(df_tails[df_tails["TestingRateInterval"]=='(10% - 15%]']))
    c4 = p3.circle(x=x, y = "Confirmed", size =10, fill_alpha = 0.7, color ="TestingColor",line_dash = [3,3], 
                   source = ColumnDataSource(df_tails[df_tails["TestingRateInterval"]=='(15% - 20%]']))
    c5 = p3.circle(x=x, y = "Confirmed", size =10, fill_alpha = 0.7, color ="TestingColor",line_dash = [3,3], 
                   source = ColumnDataSource(df_tails[df_tails["TestingRateInterval"]=='(20% and more)']))

    # Stylize the plot area
    p3.plot_width = 950                     # To change the width of the plot
    p3.plot_height = 500                    # To change the height of plot
    p3.background_fill_color = "ghostwhite"   # To add background colorto the figure
    # p.background_fill_alpha = 0.12

    # Stylize the grid
    p3.xgrid.grid_line_color = "white"
    p3.ygrid.grid_line_color = "white"
    p3.ygrid.grid_line_alpha = 0.7
    p3.xgrid.grid_line_dash = [5,3]
    p3.xgrid.grid_line_width = 2
    p3.grid.grid_line_dash = [5,3]
    p3.grid.grid_line_width = 2


    # Axes Geometry
    # p3.x_range = DataRange1d(start = 0, end = 1000 ) # x_range changes according to the active legends
    # p3.y_range = DataRange1d(only_visible=True) # y_range changes according to the active legends
    p3.y_range.start = 0

    # Stylize the axes
    p3.axis.axis_label_text_font_style = "bold" #"normal", "italic"
    p3.axis.axis_label_text_color = "black"
    # p3.xaxis.major_label_orientation = "vertical"
    # p.axis.major_label_text_font_style = "bold" # for axis' major tick marks' labels value color
    p3.yaxis.minor_tick_in = 0
    p3.yaxis.minor_tick_out = 0
    p3.xaxis.minor_tick_in = 0
    p3.xaxis.minor_tick_out = 0


    # Stylize the figure title
    p3.title.text_color = "black"
    p3.title.text_font = "times"
    p3.title.text_font_size = "20px" # px stands for pixel. Have to mention.
    p3.title.align = "center"

    legend = Legend(items=[('Zero Testing', [c0]),('(0% - 5%]', [c1]),("(5% - 10%]", [c2]), 
                           ("(10% - 15%]", [c3]), ("(15% - 20%]" , [c4]), 
                           ("(20% and more)" , [c5])
                  ])
    legend.border_line_color = None
    legend.click_policy="hide"  # To disable/hide the legend on click
    p3.add_layout(legend, 'right')

    # Stylize the tools
    # Adding customizayion to HoverTool
    p3.tools = [ZoomInTool(),ZoomOutTool(), ResetTool(), BoxZoomTool()]
    hover = HoverTool(tooltips = [("Country", "@Country"),("Confirmed Cases", "@Confirmed"),("Population Density", "@Pop_Density"),("Testing Count", "@Testing"), ("Testing Rate", "@TestingRate{0.00}")])
    p3.add_tools(hover) # Customization of HoverTool
    plots.append(p3)

# Creating separate tabs for the two figures created above
tab1 = Panel(child=plots[0], title="Population")
tab2 = Panel(child=plots[1], title="Population Density")

# Creating list of Tabs
tabs = Tabs(tabs=[ tab1, tab2 ])  

layout=column(tabs)

# Displaying the layout
show(layout) 

In [66]:
# mypalette = ['wheat', 'wheat', 'yellow', 'red', 'green']
# mypalette = ["grey", Viridis[6][5], Viridis[6][4], Viridis[6][3], Viridis[6][2]]
# mypalette = ["grey", Magma[7][2], Magma[7][4], Magma[7][5], Magma[7][6]]

# color_mapper = LinearColorMapper(palette = mypalette,low = 0, high = max(df_tails["TestingRate"]))
# color_bar = ColorBar(color_mapper=color_mapper, location = (0,0))

# p3.circle(x='Pop_Density', y="Confirmed", source=df, size = 8, color={'field': 'TestingRate', 'transform': color_mapper},
#           legend_label = "TestingColor", line_color = "black",line_dash = (4,2), alpha = 0.6
#          )
          #, color=factor_cmap('TestingStatus', mypalette, TestingStatusLevels)) # plotting the data using glyph circle
    

#     legend.background_fill_color = "#1f77b4"
#     legend.background_fill_alpha = 0.01
#     legend.label_text_font = "times"
#     legend.label_text_font_size = '12px'

# p4.add_layout(color_bar, 'right')


###### Few Insights:

- <b>Cambodia</b> has Recovered cases ~ Confirmed Cases but Testing is 0
Many countries like this


- <b>Eritria</b> - 1st East African country to tackle COVID-19
- <b>Fiji, New Zealand, Lesotho, Seychelles</b>: COVID-19 Free
- <b>Vatican City, Papua New Guinea, Saint Kitts and Nevis, Saint Lucid</b> : Confirmed Cases = Recovered -cases but officially not yet COVID free.
- <b>Laos</b>: Confirmed Cases = Recovered cases but guessed untrue


- <b>Iceland, Taiwan</b>: Recovered cases ~ Confirmed Cases

- <b>Central African Republic, Guinea Bissau, Haiti, Hondurus, Mauritania, Nepal, Zimbabwe</b>:
Recovered Cases  << compared to confirmed cases


- <b>Germany, Ireland, Sweden, Singapore, Netherland</b>: Have similar pattern in Testing Counts.
- <b>Japan, Thailand </b> also have similar pattern in testing.


- <b>South Sudan,Yemen, UK </b>: Deaths > Recovered Cases


- <b>Norway</b>: Recovered Cases shoot on 1 single day
- <b>MS Zaandam</b>: Cruise data
